# SDK Walkthrough

## Board

In [19]:
from kaggle_environments import make
from kaggle_environments.envs.halite.helpers import *

# Create a test environment for use later
board_size = 5
environment = make("halite", configuration={"size": board_size, "startingHalite": 1000})
agent_count = 2
environment.reset(agent_count)
state = environment.state[0]

In [3]:
board = Board(state.observation, environment.configuration)
def get_ship_input(player):
    '''Get user input for ship action'''
    ship_id = player.ship_ids[0]
    
    next_order = input("What to do for ship {}: ".format(ship_id))
    if next_order == 'w':
        player.ships[0].next_action = ShipAction.NORTH
    elif next_order == 's':
        player.ships[0].next_action = ShipAction.SOUTH
    elif next_order == ' ':
        player.ships[0].next_action = ShipAction.CONVERT
    

In [4]:
print(f"Player Ids: {[player.id for player in board.players.values()]}")
print(f"Ship Ids: {[ship.id for ship in board.ships.values()]}")
#Note there are currently no shipyards because our Board just initialized.
print(f"Shipyard Ids: {[shipyard.id for shipyard in board.shipyards.values()]}")
assert len(board.cells) == board_size * board_size

Player Ids: [0, 1]
Ship Ids: ['0-1', '0-2']
Shipyard Ids: []


## Point

In [5]:
point = Point(3, -4)

# Points are tuples
assert isinstance(point, tuple)
# Points have x and y getters (no setters)
assert point.x == 3
assert point.y == -4
# Points implement several common operators
assert point == Point(3, -4)
assert abs(point) == Point(3, 4)
assert -point == Point(-3, 4)
assert point + point == (6, -8)
assert point - point == Point(0, 0)
assert point * 3 == Point(9, -12)

# Point supports floordiv but not div since x and y are ints not floats
assert point // 2 == Point(1, -2)
assert point % 3 == Point(0, 2)

# Prints like a tuple
print(point)
print(board[point])

(3, -4)


## Actions

In [6]:
print([action.name for action in ShipAction])
print([action.name for action in ShipyardAction])

# Grab a ship to test with
ship = next(iter(board.ships.values()))
print(f"Initial action: {ship.next_action}")
ship.next_action = ShipAction.NORTH
print(f"New action: {ship.next_action}")

['NORTH', 'EAST', 'SOUTH', 'WEST', 'CONVERT']
['SPAWN']
Initial action: None
New action: NORTH


## Lookahead

In [23]:
next_ship.position

(1, 3)

In [24]:
next_ship.position - ShipAction.NORTH.to_point()

(1, 2)

In [7]:
print(board)
board = board.next()
print(board)

# Let's make sure we moved north!
next_ship = board.ships[ship.id]
assert next_ship.position - ship.position == ShipAction.NORTH.to_point()

# We'll use this in the next cell
ship = next_ship

# What happens if we call board.next()?
print(board.next())

| 0 | 2 | 0 | 2 | 0 |
| 0 | 0 | 0 | 0 | 0 |
| 0 |a1 | 0 |b1 | 0 |
| 0 | 0 | 0 | 0 | 0 |
| 0 | 2 | 0 | 2 | 0 |

| 0 | 2 | 0 | 2 | 0 |
| 0 |a0 | 0 | 0 | 0 |
| 0 | 1 | 0 |b1 | 0 |
| 0 | 0 | 0 | 0 | 0 |
| 0 | 2 | 0 | 2 | 0 |

| 0 | 2 | 0 | 2 | 0 |
| 0 |a0 | 0 | 0 | 0 |
| 0 | 1 | 0 |b0 | 0 |
| 0 | 0 | 0 | 0 | 0 |
| 0 | 2 | 0 | 2 | 0 |



In [8]:
ship.next_action = ShipAction.CONVERT
board = board.next()
print(board)

| 0 | 2 | 0 | 2 | 0 |
| 0 | 0A| 0 | 0 | 0 |
| 0 | 1 | 0 |b0 | 0 |
| 0 | 0 | 0 | 0 | 0 |
| 0 | 2 | 0 | 2 | 0 |



In [9]:
shipyard = board[ship.position].shipyard
shipyard.next_action = ShipyardAction.SPAWN
board = board.next()
print(board)

| 0 | 2 | 0 | 2 | 0 |
| 0 |a0A| 0 | 0 | 0 |
| 0 | 1 | 0 |b0 | 0 |
| 0 | 0 | 0 | 0 | 0 |
| 0 | 2 | 0 | 2 | 0 |



In [10]:
for ship in board.ships.values():
    ship.next_action = ShipAction.SOUTH
board = board.next()
print(board)

| 0 | 3 | 0 | 3 | 0 |
| 0 | 0A| 0 | 0 | 0 |
| 0 |a1 | 0 | 0 | 0 |
| 0 | 0 | 0 |b0 | 0 |
| 0 | 3 | 0 | 3 | 0 |



In [11]:
current_player = board.current_player
for ship in current_player.ships:
    ship.next_action = ShipAction.SOUTH
print(current_player.next_actions)

{'3-1': 'SOUTH'}


## Creating an Agent

In [22]:
def move_ships_north_agent(observation, configuration):
    board = Board(observation, configuration)
    current_player = board.current_player
    for ship in current_player.ships:
        ship.next_action = ShipAction.NORTH
    return current_player.next_actions

environment.reset(agent_count)
environment.run([move_ships_north_agent, "random"])
environment.render(mode="ipython", width = 500, height = 450)

## Board (Advanced)

In [43]:
first_player_actions = {'0-1': 'CONVERT'}
second_player_actions = {'0-2': 'NORTH'}

actions = [first_player_actions, second_player_actions]
board = Board(state.observation, environment.configuration, actions)
print(board)
print(board.next())

| 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 |
| 0 |a0 | 4 |b0 | 0 |
| 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 |

| 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 |b0 | 0 |
| 0 | 0A| 4 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 |



# Now for my own testing

In [46]:
board = board.next()

In [47]:
print(board)

| 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 |b0 | 0 |
| 0 | 0A| 4 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 |



In [48]:
print(board.shipyards)

{'1-1': <kaggle_environments.envs.halite.helpers.Shipyard object at 0x00000183F32E75E0>}


In [49]:
first_player_actions = {'1-1': 'SPAWN'}
second_player_actions = {'0-2': 'NORTH'}

actions = [first_player_actions, second_player_actions]
board = Board(board.observation, environment.configuration, actions)
print(board)
print(board.next())
board = board.next()

| 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 |b0 | 0 |
| 0 | 0A| 4 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 |

| 0 | 0 | 0 |b0 | 0 |
| 0 | 0 | 0 | 0 | 0 |
| 0 |a0A| 4 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 |



In [80]:
for p in board.players:
    for s in board.players[p].ship_ids:
        player_actions = {s: 'NORTH'}
        actions[p] = player_actions

board = Board(board.observation, environment.configuration, actions)
print(board)
print(board.next())
board = board.next()

| 0 | 0 | 0 | 0 | 0 |
| 0 |a0 | 0 | 0 | 0 |
| 0 | 0A| 5 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 |b0 | 0 |

| 0 |a0 | 0 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 |
| 0 | 0A| 5 | 0 | 0 |
| 0 | 0 | 0 |b0 | 0 |
| 0 | 0 | 0 | 0 | 0 |



In [50]:
print(board)

| 0 | 0 | 0 |b0 | 0 |
| 0 | 0 | 0 | 0 | 0 |
| 0 |a0A| 4 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 |



In [28]:
first_player_actions = {'1-1': 'SPAWN'}
second_player_actions = {'0-2': 'NORTH'}

actions = [first_player_actions, second_player_actions]
board = Board(board.observation, environment.configuration, actions)
print(board)
print(board.next())

| 0 | 0 | 0 |b0 | 0 |
| 0 | 0 | 0 | 0 | 0 |
| 0 | 0A| 4 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 |

| 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 |
| 0 |a0A| 4 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 |b0 | 0 |



In [55]:
print(board.players[0].ship_ids)

['3-1']


In [56]:
first_player_actions = {'3-1': "EAST"}
second_player_actions = {'0-2': "CONVERT"}

actions = [first_player_actions, second_player_actions]
board = Board(board.observation, environment.configuration, actions)
print(board)
print(board.next())

| 0 | 0 | 0 |b0 | 0 |
| 0 | 0 | 0 | 0 | 0 |
| 0 |a0A| 4 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 |

| 0 | 0 | 0 | 0B| 0 |
| 0 | 0 | 0 | 0 | 0 |
| 0 | 0A|a4 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 |



In [ ]:
first_player_actions = {}
second_player_actions = {'0-2': "CONVERT"}

actions = [first_player_actions, second_player_actions]
board = Board(board.observation, environment.configuration, actions)
print(board)
print(board.next())

In [30]:
current_player = board.current_player

In [31]:
print(current_player.shipyard_ids, current_player.ship_ids)

['1-1'] []


In [32]:
for sy in current_player.shipyards:
    syz.next_action = ShipyardAction.SPAWN

NameError: name 'syz' is not defined

In [33]:
print(current_player.shipyards[0].next_action)

SPAWN


In [34]:
for ship in current_player.ships:
    print(ship.next_action)


In [35]:
for shipyard in board.shipyards.values():
    print(shipyard.player_id)

0


In [36]:
for ship in board.ships.values():
    print(ship.player_id)

1


TypeError: 'type' object is not iterable

In [37]:
for sy in current_player.shipyards:
    print(sy.next_action)
    sy.next_action = ShipyardAction.SPAWN

SPAWN


In [38]:
board = board.next()
print(board)

| 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 |
| 0 |a0A| 4 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 |b0 | 0 |



In [39]:
current_player.ships[0].halite

IndexError: list index out of range

In [40]:
def get_point(line_index, board_size):
    """Get the coordinates of a cell. Inputs are the line index and board size.
    
    Halite amounts are given in 1-d list format. Transform that so the 
    coordinates can be used."""
    point_address = (line_index % board_size, line_index // board_size)
    return point_address
assert get_point(1, 5) == (1, 0)
#assert get_point(6, 5) == "(1, 1)"
#assert get_point(24, 5) == "(4, 4)"
#assert get_point(0, 5) == "(0, 0)"
#assert get_point(440, 21) == "(20, 20)"

def get_rich_cells(board):
    """Return the cell index with maximum halite"""
    rich_cells = []
    for i in range(len(board.observation['halite'])):
        if board.observation['halite'][i] == max(board.observation['halite']):
            rich_cells.append(i)
    return rich_cells

0

In [13]:
def getDirTo(fromPos, toPos, size):
    fromX, fromY = divmod(fromPos[0],size), divmod(fromPos[1],size)
    toX, toY = divmod(toPos[0],size), divmod(toPos[1],size)
    if fromY < toY: return ShipAction.NORTH
    if fromY > toY: return ShipAction.SOUTH
    if fromX < toX: return ShipAction.EAST
    if fromX > toX: return ShipAction.WEST

# Directions a ship can move
directions = [ShipAction.NORTH, ShipAction.EAST, ShipAction.SOUTH, ShipAction.WEST]

# Will keep track of whether a ship is collecting halite or carrying cargo to a shipyard
ship_states = {}


def agent(obs, config):
    size = config.size
    board = Board(obs, config)
    me = board.current_player

    # If there are no ships, use first shipyard to spawn a ship.
    if len(me.ships) == 0 and len(me.shipyards) > 0:
        me.shipyards[0].next_action = ShipyardAction.SPAWN

    # If there are no shipyards, convert first ship into shipyard.
    if len(me.shipyards) == 0 and len(me.ships) > 0:
        me.ships[0].next_action = ShipAction.CONVERT
    
    for ship in me.ships:
        if ship.next_action == None:
            
            ### Part 1: Set the ship's state 
            if ship.halite < 200: # If cargo is too low, collect halite
                ship_states[ship.id] = "COLLECT"
            if ship.halite > 500: # If cargo gets very big, deposit halite
                ship_states[ship.id] = "DEPOSIT"
                
            ### Part 2: Use the ship's state to select an action
            if ship_states[ship.id] == "COLLECT":
                # If halite at current location running low, 
                # move to the adjacent square containing the most halite
                if ship.cell.halite < 100:
                    neighbors = [ship.cell.north.halite, ship.cell.east.halite, 
                                 ship.cell.south.halite, ship.cell.west.halite]
                    best = max(range(len(neighbors)), key=neighbors.__getitem__)

                    ship.next_action = directions[best]
            if ship_states[ship.id] == "DEPOSIT":
                # Move towards shipyard to deposit cargo
                direction = getDirTo(ship.position, me.shipyards[0].position, size)
                if direction: ship.next_action = direction
                
    return me.next_actions